In [ ]:
import agh_db_lectures
agh_db_lectures.prepare_notebook_for_sql()

# Privilege Management

Consider the following scenarios.

> Multiple applications, each with its own database (i.e., catalog) are served by the same DBMS.  Every application manages its own database by, e.g., creating tables and migrating the schema to new versions on updates.

> A database for an enterprise is designed first and then multiple applications are developed to use it.  Certain employees (e.g., administrators, managers, analysts) are also given direct (SQL) access to the database.

_notes_

In the first scenario, each application can have its own user account with the DBMS.  Privileges can be configured so that the application is only able to access its own catalog.

In the second scenario the privileges can be used on a more granular level to grant access to particular tables or particular (kinds of) operations.  The concept of user roles becomes useful.

## Managing Users in MariaDB

In [ ]:
%sql mysql:///mysql?unix_socket=/var/run/mysql/mysql.sock

_notes_

We are connecting to database `mysql` (which exists by default).

In [ ]:
%%sql
SELECT Host, User, Password FROM user;

### User Creation and Privilege Assignment

In [ ]:
%%sql
CREATE USER theodore@127.0.0.1 IDENTIFIED BY 'PingVim'

_notes_

```sql
DROP USER theodore@127.0.0.1
```

```sql
SELECT PASSWORD('PingVim')
```

```sql
CREATE OR REPLACE USER theodore@127.0.0.1
IDENTIFIED BY PASSWORD '*749882C224A9E49BADB6492AAAE881F371BB7C4E'
```

```sql
CREATE USER theodore@"192.168.134.0/255.255.255.0"
IDENTIFIED BY 'S3cur3 Pa$$word3'
```

Whenever in doubt, we can quote the host or user part.

```shell
mariadb --port=23306 --host=127.0.0.1 \
    -p'S3cur3 Pa$$word3' --user=theodore mysql
```

_notes_

```shell
mariadb --port=23306 --host=127.0.0.1 \
    -p'PingVim' --user=theodore mysql
```

```sql
GRANT SELECT ON agh_it_wordpress TO theodore@127.0.0.1
```

Theodore can now connect to the catalog.

```sql
SELECT comment_ID,
       SUBSTRING(comment_content, 1, 20),
       comment_approved
FROM wp_comments;
```

But these fail.

```sql
SELECT * FROM wp_posts;
```

```sql
UPDATE wp_comments SET comment_approved = 1;
```

In [ ]:
%%sql
REVOKE SELECT ON agh_it_wordpress.* FROM theodore@127.0.0.1

In [ ]:
%%sql
CREATE OR REPLACE USER pancratius@127.0.0.1 IDENTIFIED VIA pam

_notes_

Hostname can also be matched with a `LIKE`-like pattern, e.g., `10.0.%`.

Plugins can be used to authenticate users differently.  For example, authentication through external mechanisms is possible.  The `pam` authentication plugin would use similar mechanisms as used in the (UNIX-like) host operating system.

Plugins — as one would expect — are pluggable.  Hence they need to be loaded before they can be used.  This can be done with a command or with a configuration option.

```sql
INSTALL SONAME 'auth_pam'
```

In [ ]:
%%sql
SELECT Host, User, Password, plugin, authentication_string
FROM user;

_notes_

Use of `pam` authentication would be difficult to demonstrate given our server is running in an unprivileged container.  Let's assign `pancratius@"127.0.0.1"` a casual password.

```sql
ALTER USER pancratius@"127.0.0.1"
IDENTIFIED BY 'MUCH passw0rd, VERY secur!ty'
```

```sql
GRANT SELECT ON agh_it_wordpress.wp_comments TO pancratius@"127.0.0.1";
```

In [ ]:
%%sql
GRANT GRANT OPTION ON agh_it_wordpress.wp_comments
TO theodore@127.0.0.1;

_notes_

Perform the above as `theodore@127.0.0.1`.

```sql
GRANT GRANT OPTION ON agh_it_wordpress.wp_comments
TO theodore@127.0.0.1;
SHOW GRANTS FOR theodore@127.0.0.1
```

After this `GRANT`, `theodore@127.0.0.1` can now pass forward the `SELECT` privilege on `wp_comments`.

```shell
mariadb --port=23306 --host=127.0.0.1 \
    -p'MUCH passw0rd, VERY secur!ty' --user=pancratius \
    agh_it_wordpress
```

### Privilege Types and Examples

https://mariadb.com/docs/server/reference/sql-statements/account-management-sql-statements/grant

#### Global Level

- `ALL PRIVILEGES ON *.*`
- `CREATE USER ON *.*`

#### Database Level

- `DROP ON agh_it_wordpress.*` (user can drop `agh_it_wordpress`) 
- `CREATE ON theodore_db.*` (user can create `theodore_db`)

#### Table Level

- `DELETE ON agh_it_wordpress.wp_comments`
- `DELETE ON wp_comments` (when already connected to the right db)

#### Column Level

- `UPDATE (comment_approved) ON agh_it_wordpress.wp_comments`

#### Others

Function, procedure and proxy privileges…

## User Roles

In [ ]:
%%sql
CREATE ROLE user_viewer

In [ ]:
%%sql
SELECT Host, User, Password, is_role
FROM user

_notes_

```sql
SELECT User AS role FROM user WHERE is_role = 'Y'
```

_notes_

```sql
CREATE ROLE IF NOT EXISTS user_viewer;

GRANT SELECT (ID, user_login, user_email, user_registered)
ON agh_it_wordpress.wp_users
TO user_viewer
```

```sql
GRANT user_viewer TO theodore@127.0.0.1
```

Then as, `theodore@127.0.0.1`, execute the following.

```sql
SELECT user_login FROM wp_users;
```

_notes_

Still denied.

No role is activated by default.

```sql
SELECT CURRENT_ROLE()
```

```sql
SET ROLE user_viewer;
SELECT CURRENT_ROLE();
SET ROLE NONE;
SELECT CURRENT_ROLE();
SET ROLE user_viewer;
```

In [ ]:
%%sql
CREATE ROLE site_reporter;

GRANT SELECT ON agh_it_wordpress.wp_posts TO site_reporter;

GRANT user_viewer TO site_reporter;

In [ ]:
%%sql
REVOKE user_viewer FROM theodore@127.0.0.1;
GRANT site_reporter TO theodore@127.0.0.1

_notes_

Theodore now cannot set current role to `user_viewer`, but can set to `site_reporter` and, as such, still use all the privileges of `user_viewer`, `PUBLIC`, and `reporter`.

## Major Differences in Postgres

In Postgres, when a privilege is revoked from a user, it gets revoked in a cascade fashion from those who got it from that user.

```sql
REVOKE SELECT ON products FROM eugenia CASCADE
```

_notes_

`CASCADE` is necessary, otherwise, if dependent privileges exist, the `REVOKE` command shall fail.

MariaDB currently does not have the notion of dependent privileges.